# Finetune DeepSeek Coder 1.3B for NBA Kaggle Database SQLite Generation

In [ ]:
import pandas as pd
import torch
from datasets import Dataset
from transformers import AutoTokenizer, AutoModelForCausalLM, TrainingArguments, Trainer, BitsAndBytesConfig, EarlyStoppingCallback, PreTrainedTokenizer
from torch.utils.data import DataLoader
import sys
from peft import LoraConfig, get_peft_model, TaskType
from huggingface_hub import snapshot_download
import os
import re
import contextlib #helps make pip silent
import sys
import os
import numpy as np
with contextlib.redirect_stdout(sys.__stdout__), contextlib.redirect_stderr(sys.__stderr__):
    %pip install datasets

Note: you may need to restart the kernel to use updated packages.


In [ ]:
is_google_colab = False
use_bnb = True

In [3]:
current_read_path = "./"
current_write_path = "./"

def read_path(rel_path):
    return os.path.join(current_read_path, rel_path)

def write_path(rel_path):
    return os.path.join(current_write_path, rel_path)

if is_google_colab:
    from google.colab import drive
    drive.mount('/content/drive')
    current_write_path = "/content/drive/MyDrive/sql_gen"

    hugging_face_path = snapshot_download(
        repo_id="USC-Applied-NLP-Group/SQL-Generation",
        repo_type="model",
        allow_patterns=["train-data/*", "deepseek-coder-1.3b-instruct/*"], 
    )
    sys.path.append(hugging_face_path)
    current_read_path = hugging_face_path

NameError: name 'is_google_colab' is not defined

## First define prompt

In [1]:
from src.prompts.prompt import input_text as input_prompt

print(len(input_prompt))

9035


## Load data and convert to Dataset object tokenized by the DeepSeek model

In [ ]:


# Model output directories
MODEL_DIR = write_path("fine-tuned-model-16-test")
VAL_OUTPUT = write_path("val-16.hf")

# Load dataset
df = pd.read_csv(read_path("train-data/sql_train.tsv"), sep='\t')

df = df.applymap(lambda x: re.sub(r'\s+', ' ', x) if isinstance(x, str) else x)

# Display dataset info
print(f"Total dataset examples: {len(df)}")
print(df.head())

# Load tokenizer
model_name = read_path("deepseek-coder-1.3b-instruct")
tokenizer = AutoTokenizer.from_pretrained(model_name)

# Enable 8-bit quantization for lower memory usage
bnb_config = None
if use_bnb:
    bnb_config = BitsAndBytesConfig(
        load_in_8bit=True, 
        bnb_8bit_compute_dtype=torch.float16
    )

# Load model with quantization
#device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
device_name = 'cuda' if torch.cuda.is_available() else 'cpu'
device = torch.device(device_name)
model = AutoModelForCausalLM.from_pretrained(
    model_name, 
    quantization_config=bnb_config,
    device_map=device
)

# Add a custom stop token (can be anything that won’t show up in your data)
special_token = "<|endofsql|>"

# Only add if it doesn’t already exist
#if special_token not in tokenizer.get_vocab():
print("adding!")
print(len(tokenizer))
tokenizer.add_special_tokens({"additional_special_tokens": [special_token]})
tokenizer.eos_token = special_token
model.resize_token_embeddings(len(tokenizer))
print(len(tokenizer)) 

tokenizer.truncation_side = "left"

def format_deepseek_chat(example, tokenizer, special_token="<|endofsql|>"):
    # Manually build the prompt as one flat string
    prompt = f"{input_prompt}{example['natural_query']}\n"
    completion = f"SQLite:\n{example['sql_query']}{special_token}"

    full_text = prompt + completion
    tokenized = tokenizer(
        full_text,
        truncation=True,
        padding="max_length",
        max_length=3156,  # or whatever your model can handle
    )

    # Mask out prompt tokens in the labels
    prompt_len = len(tokenizer(prompt, truncation=True)["input_ids"])
    labels = tokenized["input_ids"][:]
    labels[:prompt_len] = [-100] * prompt_len
    tokenized["labels"] = labels

    return tokenized

# Build dataset dict
dataset_dict = {
    "natural_query": df["natural_query"].tolist(),
    "sql_query": df["sql_query"].tolist(),
}

# Create HuggingFace Dataset
dataset = Dataset.from_dict(dataset_dict)

# Apply formatting
tokenized_dataset = dataset.map(
    lambda x: format_deepseek_chat(x, tokenizer),
    remove_columns=["natural_query", "sql_query"]
)

# Split into train/validation
split = int(0.9 * len(tokenized_dataset))  # 90% train, 10% validation
train_dataset = tokenized_dataset.select(range(split))
val_dataset = tokenized_dataset.select(range(split, len(tokenized_dataset)))

print(len(train_dataset))
print(len(val_dataset))

for v in val_dataset:
    print(v)
    break

/var/folders/g0/47tr69v179dg7w6zyphp9b280000gn/T/ipykernel_35112/48906000.py:8: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df = df.applymap(lambda x: re.sub(r'\s+', ' ', x) if isinstance(x, str) else x)


Total dataset examples: 1044
                                       natural_query  \
0  Which NBA teams were established after the yea...   
1  What is the most points the Los Angeles Lakers...   
2  What is the second-highest number of points th...   
3  How many home games did the Golden State Warri...   
4  What is the average number of assists by the B...   

                                           sql_query                result  
0  SELECT full_name FROM team WHERE year_founded ...  New Orleans Pelicans  
1  SELECT MAX(pts_home) FROM game WHERE team_name...                   162  
2  SELECT pts_home FROM game WHERE team_name_home...                   156  
3  SELECT COUNT(*) FROM game WHERE team_abbreviat...                    29  
4  SELECT AVG(ast_home) FROM game WHERE team_abbr...           26.51355662  
adding!
32022
32023


Map: 100%|██████████| 1044/1044 [00:17<00:00, 59.19 examples/s]

939
105
{'input_ids': [32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 3201

## Load model and define training arguments

In [3]:
# Define LoRA configuration
lora_config = LoraConfig(
    r=16,  # Rank of LoRA matrices (adjust for memory vs. accuracy)
    lora_alpha=32,  # Scaling factor
    lora_dropout=0.0,  # Dropout for regularization
    bias="none",
    task_type=TaskType.CAUSAL_LM,
    target_modules=[
        "q_proj",
        "k_proj",
        "v_proj",
        "o_proj",
        "gate_proj",
        "up_proj",
        "down_proj"
    ]
)

# Wrap model with LoRA adapters
model = get_peft_model(model, lora_config)
model = model.to(device)
model.print_trainable_parameters()  # Show trainable parameters count

trainable params: 14,991,360 || all params: 1,360,508,928 || trainable%: 1.1019


## Setup model trainer

In [4]:
training_args = TrainingArguments(
    output_dir=MODEL_DIR,
    evaluation_strategy="epoch",  # Evaluate at the end of each epoch
    save_strategy="epoch",  # Save model every epoch
    per_device_train_batch_size=1,  # LoRA allows higher batch size
    per_device_eval_batch_size=1,
    gradient_accumulation_steps=16,
    num_train_epochs=10,  # Increase if needed
    learning_rate=5e-5,  # Higher LR since we're only training LoRA layers
    weight_decay=0.001,
    logging_steps=50,  # Print loss every 50 steps
    save_total_limit=2,  # Keep last 4 checkpoints
    bf16=True if torch.cuda.is_available() else False,
    push_to_hub=False,
    load_best_model_at_end=True,
    metric_for_best_model="eval_loss",
    greater_is_better=False
)

# Trainer setup
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=val_dataset,
    tokenizer=tokenizer,
    callbacks=[EarlyStoppingCallback(early_stopping_patience=2)]
)

c:\Users\Dean\AppData\Local\Programs\Python\Python312\Lib\site-packages\transformers\training_args.py:1611: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
C:\Users\Dean\AppData\Local\Temp\ipykernel_6496\510577166.py:21: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Trainer.__init__`. Use `processing_class` instead.
  trainer = Trainer(
No label_names provided for model class `PeftModelForCausalLM`. Since `PeftModel` hides base models input arguments, if label_names is not given, label_names can't be set automatically within `Trainer`. Note that empty label_names list will be used instead.


## Run fine-tuning and save model weights when complete

In [5]:
# Run training
trainer.train()

# Merge LoRA adapters with the base model before saving
model = model.merge_and_unload()
model.save_pretrained(MODEL_DIR)
tokenizer.save_pretrained(MODEL_DIR)

c:\Users\Dean\AppData\Local\Programs\Python\Python312\Lib\site-packages\transformers\integrations\sdpa_attention.py:54: UserWarning: 1Torch was not compiled with flash attention. (Triggered internally at C:\actions-runner\_work\pytorch\pytorch\builder\windows\pytorch\aten\src\ATen\native\transformers\cuda\sdp_utils.cpp:555.)
  attn_output = torch.nn.functional.scaled_dot_product_attention(
c:\Users\Dean\AppData\Local\Programs\Python\Python312\Lib\site-packages\bitsandbytes\autograd\_functions.py:315: UserWarning: MatMul8bitLt: inputs will be cast from torch.bfloat16 to float16 during quantization
  warnings.warn(f"MatMul8bitLt: inputs will be cast from {A.dtype} to float16 during quantization")
c:\Users\Dean\AppData\Local\Programs\Python\Python312\Lib\site-packages\bitsandbytes\autograd\_functions.py:315: UserWarning: MatMul8bitLt: inputs will be cast from torch.float32 to float16 during quantization
  warnings.warn(f"MatMul8bitLt: inputs will be cast from {A.dtype} to float16 during q

c:\Users\Dean\AppData\Local\Programs\Python\Python312\Lib\site-packages\peft\utils\save_and_load.py:250: UserWarning: Setting `save_embedding_layers` to `True` as the embedding layer has been resized during finetuning.
  warnings.warn(
c:\Users\Dean\AppData\Local\Programs\Python\Python312\Lib\site-packages\bitsandbytes\autograd\_functions.py:315: UserWarning: MatMul8bitLt: inputs will be cast from torch.bfloat16 to float16 during quantization
  warnings.warn(f"MatMul8bitLt: inputs will be cast from {A.dtype} to float16 during quantization")
c:\Users\Dean\AppData\Local\Programs\Python\Python312\Lib\site-packages\bitsandbytes\autograd\_functions.py:315: UserWarning: MatMul8bitLt: inputs will be cast from torch.float32 to float16 during quantization
  warnings.warn(f"MatMul8bitLt: inputs will be cast from {A.dtype} to float16 during quantization")
c:\Users\Dean\AppData\Local\Programs\Python\Python312\Lib\site-packages\peft\utils\save_and_load.py:250: UserWarning: Setting `save_embedding_l

('./fine-tuned-model-16\\tokenizer_config.json',
 './fine-tuned-model-16\\special_tokens_map.json',
 './fine-tuned-model-16\\tokenizer.json')

## Try inference using fine-tuned model

In [6]:
model = AutoModelForCausalLM.from_pretrained(MODEL_DIR, torch_dtype=torch.bfloat16, device_map=device)
tokenizer = AutoTokenizer.from_pretrained(MODEL_DIR)

# Prepare query with the same prompt
input_text = "How many points do the Los Angeles Lakers average at home?"
message = [{'role': 'user', 'content': input_prompt + input_text}]
inputs = tokenizer.apply_chat_template(message, add_generation_prompt=True, return_tensors="pt").to(model.device)

# Generate SQL query
outputs = model.generate(
    inputs,
    max_new_tokens=256,
    eos_token_id=tokenizer.convert_tokens_to_ids("<|endofsql|>")
)
model_output = tokenizer.decode(outputs[0][len(inputs[0]):], skip_special_tokens=True)

print("Generated SQL:", model_output)

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:32022 for open-end generation.
The attention mask is not set and cannot be inferred from input because pad token is same as eos token. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
c:\Users\Dean\AppData\Local\Programs\Python\Python312\Lib\site-packages\bitsandbytes\autograd\_functions.py:315: UserWarning: MatMul8bitLt: inputs will be cast from torch.bfloat16 to float16 during quantization
  warnings.warn(f"MatMul8bitLt: inputs will be cast from {A.dtype} to float16 during quantization")


Generated SQL: SQLite:
SELECT AVG(pts_home) FROM game WHERE team_name_home = 'Los Angeles Lakers';ometimes
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!
!


## Save validation set to disk

In [7]:
val_dataset.save_to_disk(VAL_OUTPUT)

Saving the dataset (1/1 shards): 100%|██████████| 105/105 [00:00<00:00, 11055.38 examples/s]


## Test logic for obtaining original prompt and SQLite

In [ ]:
import sqlite3 as sql

prompt_length = len(input_prompt)

print(prompt_length)

# Create connection to sqlite3 database
connection = sql.connect(read_path('nba-data/nba.sqlite'))
cursor = connection.cursor()

for v in val_dataset:
    full_example = tokenizer.decode(v["input_ids"], skip_special_tokens=True)
    user_prompt = full_example[:prompt_length]
    question, sql_query = full_example[prompt_length:].split("SQLite:\n")
    print(question)
    print(sql_query)
    cursor.execute(sql_query)
    rows = cursor.fetchall()
    for row in rows:
        print(row)
    break

9035
How many total points did the Chicago Bulls score during the 1996 season?

SELECT SUM(pts) AS total_points FROM ( SELECT pts_home AS pts FROM game WHERE team_abbreviation_home = 'CHI' AND season_id = '21996' UNION ALL SELECT pts_away AS pts FROM game WHERE team_abbreviation_away = 'CHI' AND season_id = '21996' );
(8458.0,)


## Run evaluation over entire validation set

In [9]:
import math
import random

def compare_result(sample_query, model_output):
    # Clean model output to only have the query output
    if model_output[0:8] == "SQLite:\n":
        query = model_output[8:]
    elif model_output[0:8] == "SQLite: ":
        query = model_output[8:]
    elif model_output[0:7] == "SQLite:":
        query = model_output[7:]
    elif model_output[0:5] == "SQL:\n":
        query = model_output[5:]
    elif model_output[0:5] == "SQL: ":
        query = model_output[5:]
    elif model_output[0:4] == "SQL:":
        query = model_output[4:]
    else:
        query = model_output

    # Clean any excess text after the query semicolon
    for i in range(len(query)):
        if query[i] == ";":
            query = query[:i+1]
            break

    # Get sample and model result
    cursor.execute(sample_query)
    sample_result = [str(item) for tup in cursor.fetchall() for item in tup]

    try:
        cursor.execute(query)
    except:
        return False, False, False
    model_result = [str(item) for tup in cursor.fetchall() for item in tup]

    print(sample_result)
    print(model_result)

    # Strip all whitespace before comparing queries since there may be differences in spacing, newlines, tabs, etc.
    query = query.replace(" ", "").replace("\n", "").replace("\t", "")
    sample_query = sample_query.replace(" ", "").replace("\n", "").replace("\t", "")
    query_match = (query == sample_query)

    # If the queries match, the results clearly also match
    if query_match:
        return True, True, True

    # Try to execute query, if it fails, then this is a failure of the model
    try:
        for r in sample_result:
            for res in model_result:
                try:
                    if math.isclose(float(r), float(res), abs_tol=0.5):
                        return True, False, True
                except:
                    if r in res or res in r:
                        return True, False, True
        return True, False, False
    except:
        return True, False, False
    
num_valid = 0
num_sql_matched = 0
num_result_matched = 0

for v in val_dataset:
    # Obtain sample natural language question and sql_query
    #v = val_dataset[random.randint(0, len(val_dataset) - 1)]
    full_example = tokenizer.decode(v["input_ids"], skip_special_tokens=True)
    user_prompt = full_example[:prompt_length]
    question, sql_query = full_example[prompt_length:].split("SQLite:\n")
    #print(question)
    #print(sql_query)

    # Obtain model output
    input_text = "How many points to the Los Angeles Lakers average at home?"
    message = [{'role': 'user', 'content': input_prompt + question}]
    inputs = tokenizer.apply_chat_template(message, add_generation_prompt=True, return_tensors="pt").to(model.device)

    # Generate SQL query
    outputs = model.generate(
        inputs,
        max_new_tokens=256,
        eos_token_id=tokenizer.convert_tokens_to_ids("<|endofsql|>")
    )
    model_output = tokenizer.decode(outputs[0][len(inputs[0]):], skip_special_tokens=True)

    print(sql_query)
    print(model_output.split(";")[0])
    #print()
    #print(model_output)
    result = compare_result(sql_query, model_output)
    print("Statement valid? " + str(result[0]))
    print("SQLite matched? " + str(result[1]))
    print("Result matched? " + str(result[2]))
    print()
    print()

    if result[0]:
        num_valid += 1
    if result[1]:
        num_sql_matched += 1
    if result[2]:
        num_result_matched += 1

print("Percent valid: " + str(num_valid / len(val_dataset)))
print("Percent SQLite matched: " + str(num_sql_matched / len(val_dataset)))
print("Percent result matched: " + str(num_result_matched / len(val_dataset)))

#    break

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:32022 for open-end generation.
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:32022 for open-end generation.


SELECT SUM(pts) AS total_points FROM ( SELECT pts_home AS pts FROM game WHERE team_abbreviation_home = 'CHI' AND season_id = '21996' UNION ALL SELECT pts_away AS pts FROM game WHERE team_abbreviation_away = 'CHI' AND season_id = '21996' );
SQLite:
SELECT SUM(pts_home + pts_away) AS total_points FROM game WHERE team_name_home = 'Chicago Bulls' AND season_id = '21996'
['8458.0']
['8002.0']
Statement valid? True
SQLite matched? False
Result matched? False




The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:32022 for open-end generation.


SELECT SUM(fg3a) AS total_three_attempts FROM ( SELECT fg3a_home AS fg3a FROM game WHERE team_abbreviation_home = 'GSW' AND season_id = '22017' UNION ALL SELECT fg3a_away AS fg3a FROM game WHERE team_abbreviation_away = 'GSW' AND season_id = '22017' );
SQLite:
SELECT SUM(fg3a_home) AS total_three_pointers FROM game WHERE team_name_home = 'Golden State Warriors' AND season_id = '22017'
['2369.0']
['1136.0']
Statement valid? True
SQLite matched? False
Result matched? False




The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:32022 for open-end generation.


...

SELECT game_id, (tov_home + tov_away + stl_home + stl_away) AS total FROM game ORDER BY total DESC LIMIT 1;
SQLite:
SELECT game_id FROM other_stats ORDER BY (tov_home + tov_away + stl_home + stl_away) DESC LIMIT 1
Statement valid? False
SQLite matched? False
Result matched? False




The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:32022 for open-end generation.


SELECT MAX(other_stats.largest_lead_home) FROM other_stats JOIN game ON other_stats.game_id = game.game_id WHERE game.team_name_home = 'Golden State Warriors' AND game.season_id = '22018';
SQLite:
SELECT MAX(largest_lead_home) FROM other_stats WHERE team_abbreviation_home = 'GSW' AND season_id = '22018'
Statement valid? False
SQLite matched? False
Result matched? False




The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:32022 for open-end generation.


SELECT team_name_home, MAX(pts_fb_home) FROM other_stats JOIN game ON other_stats.game_id = game.game_id WHERE game.season_id = '22020';
SQLite:
SELECT team_name_home FROM other_stats WHERE season_id = '22020' AND pts_fb_home = (SELECT MAX(pts_fb_home) FROM other_stats WHERE season_id = '22020')
Statement valid? False
SQLite matched? False
Result matched? False


SELECT MAX(ast_home) FROM game WHERE team_name_home = 'Indiana Pacers';
SQLite:
SELECT MAX(ast_home) FROM game WHERE team_name_home = 'Indiana Pacers'
['44.0']
['44.0']
Statement valid? True
SQLite matched? True
Result matched? True


Percent valid: 0.8476190476190476
Percent SQLite matched: 0.1523809523809524
Percent result matched: 0.5428571428571428


## Test validation set only on short queries

In [10]:
num_valid = 0
num_sql_matched = 0
num_result_matched = 0
counter = 0
for v in val_dataset:
    # Obtain sample natural language question and sql_query
    #v = val_dataset[random.randint(0, len(val_dataset) - 1)]
    full_example = tokenizer.decode(v["input_ids"], skip_special_tokens=True)
    user_prompt = full_example[:prompt_length]
    question, sql_query = full_example[prompt_length:].split("SQLite:\n")
    #print(question)
    #print(sql_query)

    if len(sql_query) <= 90:
        # Obtain model output
        input_text = "How many points to the Los Angeles Lakers average at home?"
        message = [{'role': 'user', 'content': input_prompt + question}]
        inputs = tokenizer.apply_chat_template(message, add_generation_prompt=True, return_tensors="pt").to(model.device)

        # Generate SQL query
        outputs = model.generate(
            inputs,
            max_new_tokens=256,
            eos_token_id=tokenizer.convert_tokens_to_ids("<|endofsql|>")
        )
        model_output = tokenizer.decode(outputs[0][len(inputs[0]):], skip_special_tokens=True)

        print(sql_query)
        print(model_output.split(";")[0])
        #print()
        #print(model_output)
        result = compare_result(sql_query, model_output)
        print("Statement valid? " + str(result[0]))
        print("SQLite matched? " + str(result[1]))
        print("Result matched? " + str(result[2]))
        print()
        print()
        counter += 1

        if result[0]:
            num_valid += 1
        if result[1]:
            num_sql_matched += 1
        if result[2]:
            num_result_matched += 1

print("Percent valid: " + str(num_valid / counter))
print("Percent SQLite matched: " + str(num_sql_matched / counter))
print("Percent result matched: " + str(num_result_matched / counter))

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:32022 for open-end generation.
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:32022 for open-end generation.


SELECT MAX(fg_pct_home) FROM game WHERE team_name_home = 'Miami Heat';
SQLite:
SELECT MAX(fg_pct_home) FROM game WHERE team_name_home = 'Miami Heat'
['0.675']
['0.675']
Statement valid? True
SQLite matched? True
Result matched? True




The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:32022 for open-end generation.


SELECT MAX(pts_home) FROM game WHERE team_abbreviation_home = 'GSW';
SQLite:
SELECT MAX(pts_home) FROM game WHERE team_name_home = 'Golden State Warriors'
['149.0']
['155.0']
Statement valid? True
SQLite matched? False
Result matched? False




The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:32022 for open-end generation.


...

SELECT MAX(stl_away) FROM game;
SQLite:
SELECT MAX(stl_away) FROM game
['27.0']
['27.0']
Statement valid? True
SQLite matched? True
Result matched? True




The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:32022 for open-end generation.


SELECT COUNT(*) FROM game WHERE pts_home >= 120 AND pts_away >= 120;
SQLite:
SELECT COUNT(*) FROM game WHERE pts_home >= 120 AND pts_away >= 120
['3043']
['3043']
Statement valid? True
SQLite matched? True
Result matched? True




The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:32022 for open-end generation.


SELECT COUNT(*) FROM game WHERE ast_home >= 30 OR ast_away >= 30;
SQLite:
SELECT COUNT(*) FROM game WHERE ast_home >= 30 OR ast_away >= 30
['11305']
['11305']
Statement valid? True
SQLite matched? True
Result matched? True


SELECT MAX(ast_home) FROM game WHERE team_name_home = 'Indiana Pacers';
SQLite:
SELECT MAX(ast_home) FROM game WHERE team_name_home = 'Indiana Pacers'
['44.0']
['44.0']
Statement valid? True
SQLite matched? True
Result matched? True


Percent valid: 0.8275862068965517
Percent SQLite matched: 0.4827586206896552
Percent result matched: 0.7586206896551724
